In [2]:
import pandas as pd 
import numpy as np

## Lectura del archivo csv que contiene el data frame

In [3]:
df = pd.read_csv (r'C:\Users\josgr\Desktop\PI_ML_OPS\data_cruda\movies_dataset.csv')
movies = df.copy()

C:\Users\josgr\AppData\Local\Temp\ipykernel_5852\1573576912.py:1: DtypeWarning: Columns (10) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv (r'C:\Users\josgr\Desktop\PI_ML_OPS\data_cruda\movies_dataset.csv')


## Visualización de todas las columnas del data frame 

In [4]:
# Configuración para mostrar todas las columnas
pd.set_option('display.max_columns', None)

# Visualizar el DataFrame completo
movies.head(1)


adult                              belongs_to_collection    budget  \
0  False  {'id': 10194, 'name': 'Toy Story Collection', ...  30000000   

                                              genres  \
0  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...   

                               homepage   id    imdb_id original_language  \
0  http://toystory.disney.com/toy-story  862  tt0114709                en   

  original_title                                           overview  \
0      Toy Story  Led by Woody, Andy's toys live happily in his ...   

  popularity                       poster_path  \
0  21.946943  /rhIRbceoE9lR4veEXuwCC2wARtG.jpg   

                             production_companies  \
0  [{'name': 'Pixar Animation Studios', 'id': 3}]   

                                production_countries release_date  \
0  [{'iso_3166_1': 'US', 'name': 'United States o...   1995-10-30   

       revenue  runtime                          spoken_languages    status  \
0  373554033.0     81.0  [{'iso_639_1': 'en', 'name': 'English'}]  Released   

  tagline      title  video  vote_average  vote_count  
0     NaN  Toy Story  False           7.7      5415.0

## Visualizacion de las ultimas filas

In [5]:
movies.tail(1)

adult belongs_to_collection budget genres homepage      id    imdb_id  \
45465  False                   NaN      0     []      NaN  461257  tt6980792   

      original_language original_title  \
45465                en       Queerama   

                                                overview popularity  \
45465  50 years after decriminalisation of homosexual...   0.163015   

                            poster_path production_companies  \
45465  /s5UkZt6NTsrS7ZF0Rh8nzupRlIU.jpg                   []   

                                   production_countries release_date  revenue  \
45465  [{'iso_3166_1': 'GB', 'name': 'United Kingdom'}]   2017-06-09      0.0   

       runtime                          spoken_languages    status tagline  \
45465     75.0  [{'iso_639_1': 'en', 'name': 'English'}]  Released     NaN   

          title  video  vote_average  vote_count  
45465  Queerama  False           0.0         0.0

## Solicitar información completa de la estructura para su comprensión

In [6]:
movies.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 45466 entries, 0 to 45465
Data columns (total 24 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   adult                  45466 non-null  object 
 1   belongs_to_collection  4494 non-null   object 
 2   budget                 45466 non-null  object 
 3   genres                 45466 non-null  object 
 4   homepage               7782 non-null   object 
 5   id                     45466 non-null  object 
 6   imdb_id                45449 non-null  object 
 7   original_language      45455 non-null  object 
 8   original_title         45466 non-null  object 
 9   overview               44512 non-null  object 
 10  popularity             45461 non-null  object 
 11  poster_path            45080 non-null  object 
 12  production_companies   45463 non-null  object 
 13  production_countries   45463 non-null  object 
 14  release_date           45379 non-null  object 
 15  re

## Inicio de la etapa de limpieza y transformación de la data

## Visualizamos el contenido de las columnas que contienen la información anidada

In [7]:
movies_subset = movies.loc[:1, ['belongs_to_collection', 'genres', 'production_companies', 'production_countries', 'spoken_languages']]
movies_subset

belongs_to_collection  \
0  {'id': 10194, 'name': 'Toy Story Collection', ...   
1                                                NaN   

                                              genres  \
0  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...   
1  [{'id': 12, 'name': 'Adventure'}, {'id': 14, '...   

                                production_companies  \
0     [{'name': 'Pixar Animation Studios', 'id': 3}]   
1  [{'name': 'TriStar Pictures', 'id': 559}, {'na...   

                                production_countries  \
0  [{'iso_3166_1': 'US', 'name': 'United States o...   
1  [{'iso_3166_1': 'US', 'name': 'United States o...   

                                    spoken_languages  
0           [{'iso_639_1': 'en', 'name': 'English'}]  
1  [{'iso_639_1': 'en', 'name': 'English'}, {'iso...

## Procedemos a desanidar las información contenida en las columnas que contienen listas o diccionarios

In [8]:
import json

def desanidar_columna(df, columna):   # Creamos la función para desanidar cada columna
    if columna in df.columns:
        if isinstance(df[columna].iloc[0], str):  # Verificar si la columna es una cadena
            try:
                df[columna] = df[columna].apply(lambda x: [] if pd.isna(x) else json.loads(x.replace("'", '"')))
                desanidado_df = df[columna].apply(pd.Series).stack().apply(pd.Series).reset_index(drop=True)
                df.drop(columns=columna, inplace=True)
                df = pd.concat([df, desanidado_df], axis=1)
            except json.JSONDecodeError:
                print(f"Error: JSON inválido en la columna '{columna}'")
    return df

# Columnas a desanidar
columns_to_desanidar = ['belongs_to_collection', 'production_companies', 'production_countries', 'spoken_languages']

# Desanidar cada columna en el DataFrame original
for columna in columns_to_desanidar:
    movies = desanidar_columna(movies, columna)

# Imprimir el DataFrame modificado
movies.head(1)


Error: JSON inválido en la columna 'belongs_to_collection'
Error: JSON inválido en la columna 'production_companies'
Error: JSON inválido en la columna 'production_countries'
Error: JSON inválido en la columna 'spoken_languages'


adult                              belongs_to_collection    budget  \
0  False  {'id': 10194, 'name': 'Toy Story Collection', ...  30000000   

                                              genres  \
0  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...   

                               homepage   id    imdb_id original_language  \
0  http://toystory.disney.com/toy-story  862  tt0114709                en   

  original_title                                           overview  \
0      Toy Story  Led by Woody, Andy's toys live happily in his ...   

  popularity                       poster_path  \
0  21.946943  /rhIRbceoE9lR4veEXuwCC2wARtG.jpg   

                             production_companies  \
0  [{'name': 'Pixar Animation Studios', 'id': 3}]   

                                production_countries release_date  \
0  [{'iso_3166_1': 'US', 'name': 'United States o...   1995-10-30   

       revenue  runtime                          spoken_languages    status  \
0  373554033.0     81.0  [{'iso_639_1': 'en', 'name': 'English'}]  Released   

  tagline      title  video  vote_average  vote_count  
0     NaN  Toy Story  False           7.7      5415.0

## Tratamiento de valores nulos

In [9]:
# Rellenar valores nulos de los campos 'revenue' y 'budget' con 0
movies['revenue'].fillna(0, inplace=True)
movies['budget'].fillna(0, inplace=True)

# Eliminar filas con valores nulos en el campo 'release_date'
movies.dropna(subset=['release_date'], inplace=True)


## Creamos una nueva columna realease_year

In [10]:
# Convertir el campo 'release_date' al formato AAAA-mm-dd
movies['release_date'] = pd.to_datetime(movies['release_date'], errors='coerce').dt.strftime('%Y-%m-%d')

# Crear la columna 'release_year' extrayendo el año de la fecha de estreno
movies['release_year'] = pd.to_datetime(movies['release_date']).dt.year


## Creación de la nueva columna return

In [11]:
def safe_division(x, y):
    if y != 0:
        return x / y
    else:
        return 0

# Rellenar los valores nulos en los campos 'revenue' y 'budget' con 0
movies['revenue'].fillna(0, inplace=True)
movies['budget'].fillna(0, inplace=True)

# Convertir el campo 'budget' a tipo numérico
movies['budget'] = pd.to_numeric(movies['budget'], errors='coerce')

# Calcular el retorno de inversión
movies['return'] = movies.apply(lambda row: safe_division(row['revenue'], row['budget']), axis=1)



## Eliminamos los campos que no serán necesarios

In [12]:
columns_to_drop = ['video', 'imdb_id', 'adult', 'original_title', 'poster_path', 'homepage']
movies.drop(columns=columns_to_drop, inplace=True)

## Visualizamos nuestro data frame luego de limpiar y transformar

In [13]:
movies.head(1)

belongs_to_collection      budget  \
0  {'id': 10194, 'name': 'Toy Story Collection', ...  30000000.0   

                                              genres   id original_language  \
0  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...  862                en   

                                            overview popularity  \
0  Led by Woody, Andy's toys live happily in his ...  21.946943   

                             production_companies  \
0  [{'name': 'Pixar Animation Studios', 'id': 3}]   

                                production_countries release_date  \
0  [{'iso_3166_1': 'US', 'name': 'United States o...   1995-10-30   

       revenue  runtime                          spoken_languages    status  \
0  373554033.0     81.0  [{'iso_639_1': 'en', 'name': 'English'}]  Released   

  tagline      title  vote_average  vote_count  release_year     return  
0     NaN  Toy Story           7.7      5415.0        1995.0  12.451801

## Aplicamos las transformaciones necesarias para el data set credits

In [14]:
df1 = pd.read_csv(r'C:\Users\josgr\Desktop\PI_ML_OPS\data_cruda\credits.csv')
credits = df1.copy()

In [15]:
credits.head(1)


cast  \
0  [{'cast_id': 14, 'character': 'Woody (voice)',...   

                                                crew   id  
0  [{'credit_id': '52fe4284c3a36847f8024f49', 'de...  862

In [16]:
# Imprimir el contenido completo de la columna 'cast'
pd.set_option('display.max_colwidth', None)  # Para mostrar todo el contenido de las celdas


credits.loc[0, ['cast', 'crew']]

cast                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    

In [17]:
import ast

# Transformar las columnas 'cast' y 'crew' en listas de diccionarios
credits['cast'] = credits['cast'].apply(lambda x: ast.literal_eval(x))
credits['crew'] = credits['crew'].apply(lambda x: ast.literal_eval(x))

In [18]:
# Crear una nueva columna llamada "actors"
credits['actors'] = credits['cast'].apply(lambda x: x[0]['name'] if len(x) > 0 else None)


In [19]:
# Crear una nueva columna llamada "director"
credits['director'] = credits['crew'].apply(lambda x: [c['name'] for c in x if c['job'] == 'Director'][0] if any(c['job'] == 'Director' for c in x) else None)


In [20]:
#Visualizamos el resultado
print(credits[['actors', 'director']])


                 actors          director
0             Tom Hanks     John Lasseter
1        Robin Williams      Joe Johnston
2        Walter Matthau     Howard Deutch
3       Whitney Houston   Forest Whitaker
4          Steve Martin     Charles Shyer
...                 ...               ...
45471      Leila Hatami  Hamid Nematollah
45472      Angel Aquino          Lav Diaz
45473     Erika Eleniak    Mark L. Lester
45474  Iwan Mosschuchin  Yakov Protazanov
45475              None     Daisy Asquith

[45476 rows x 2 columns]


## Realizamos un merge por medio del campo id

In [21]:
# Filtrar los registros no numéricos en la columna 'id' del data set 'movies'
non_numeric_ids = movies['id'].str.contains('[^0-9]')
invalid_ids = movies[non_numeric_ids]['id']
print('Registros con IDs no numéricos:')
print(invalid_ids)

# Eliminar los registros con IDs no numéricos del data set 'movies'
movies = movies[~non_numeric_ids]

# Convertir el tipo de datos del campo 'id' en el data set 'movies'
movies['id'] = movies['id'].astype(int)

# Fusionar los data sets 'credits' y 'movies' utilizando el campo 'id'
merged_data = pd.merge(credits, movies, on='id')

# Verificar el resultado de la fusión
merged_data.head(1)



Registros con IDs no numéricos:
19730    1997-08-20
29503    2012-09-29
35587    2014-01-01
Name: id, dtype: object


cast  \
0  [{'cast_id': 14, 'character': 'Woody (voice)', 'credit_id': '52fe4284c3a36847f8024f95', 'gender': 2, 'id': 31, 'name': 'Tom Hanks', 'order': 0, 'profile_path': '/pQFoyx7rp09CJTAb932F2g8Nlho.jpg'}, {'cast_id': 15, 'character': 'Buzz Lightyear (voice)', 'credit_id': '52fe4284c3a36847f8024f99', 'gender': 2, 'id': 12898, 'name': 'Tim Allen', 'order': 1, 'profile_path': '/uX2xVf6pMmPepxnvFWyBtjexzgY.jpg'}, {'cast_id': 16, 'character': 'Mr. Potato Head (voice)', 'credit_id': '52fe4284c3a36847f8024f9d', 'gender': 2, 'id': 7167, 'name': 'Don Rickles', 'order': 2, 'profile_path': '/h5BcaDMPRVLHLDzbQavec4xfSdt.jpg'}, {'cast_id': 17, 'character': 'Slinky Dog (voice)', 'credit_id': '52fe4284c3a36847f8024fa1', 'gender': 2, 'id': 12899, 'name': 'Jim Varney', 'order': 3, 'profile_path': '/eIo2jVVXYgjDtaHoF19Ll9vtW7h.jpg'}, {'cast_id': 18, 'character': 'Rex (voice)', 'credit_id': '52fe4284c3a36847f8024fa5', 'gender': 2, 'id': 12900, 'name': 'Wallace Shawn', 'order': 4, 'profile_path': '/oGE6JqPP2xH4tNORKNqxbNPYi7u.jpg'}, {'cast_id': 19, 'character': 'Hamm (voice)', 'credit_id': '52fe4284c3a36847f8024fa9', 'gender': 2, 'id': 7907, 'name': 'John Ratzenberger', 'order': 5, 'profile_path': '/yGechiKWL6TJDfVE2KPSJYqdMsY.jpg'}, {'cast_id': 20, 'character': 'Bo Peep (voice)', 'credit_id': '52fe4284c3a36847f8024fad', 'gender': 1, 'id': 8873, 'name': 'Annie Potts', 'order': 6, 'profile_path': '/eryXT84RL41jHSJcMy4kS3u9y6w.jpg'}, {'cast_id': 26, 'character': 'Andy (voice)', 'credit_id': '52fe4284c3a36847f8024fc1', 'gender': 0, 'id': 1116442, 'name': 'John Morris', 'order': 7, 'profile_path': '/vYGyvK4LzeaUCoNSHtsuqJUY15M.jpg'}, {'cast_id': 22, 'character': 'Sid (voice)', 'credit_id': '52fe4284c3a36847f8024fb1', 'gender': 2, 'id': 12901, 'name': 'Erik von Detten', 'order': 8, 'profile_path': '/twnF1ZaJ1FUNUuo6xLXwcxjayBE.jpg'}, {'cast_id': 23, 'character': 'Mrs. Davis (voice)', 'credit_id': '52fe4284c3a36847f8024fb5', 'gender': 1, 'id': 12133, 'name': 'Laurie Metcalf', 'order': 9, 'profile_path': '/unMMIT60eoBM2sN2nyR7EZ2BvvD.jpg'}, {'cast_id': 24, 'character': 'Sergeant (voice)', 'credit_id': '52fe4284c3a36847f8024fb9', 'gender': 2, 'id': 8655, 'name': 'R. Lee Ermey', 'order': 10, 'profile_path': '/r8GBqFBjypLUP9VVqDqfZ7wYbSs.jpg'}, {'cast_id': 25, 'character': 'Hannah (voice)', 'credit_id': '52fe4284c3a36847f8024fbd', 'gender': 1, 'id': 12903, 'name': 'Sarah Freeman', 'order': 11, 'profile_path': None}, {'cast_id': 27, 'character': 'TV Announcer (voice)', 'credit_id': '52fe4284c3a36847f8024fc5', 'gender': 2, 'id': 37221, 'name': 'Penn Jillette', 'order': 12, 'profile_path': '/zmAaXUdx12NRsssgHbk1T31j2x9.jpg'}]   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        

## Verificamos si en nuestro data set tenemos duplicados, nulos o valores intercambiados entre columnas y eliminamos los duplicados y reubicamos los datos extrapolados

In [22]:
# Convertir columnas con listas en cadenas de texto
merged_data = merged_data.astype(str)

# Verificar duplicados en todas las columnas
duplicates = merged_data.duplicated()
if duplicates.any():
    print("Se encontraron registros duplicados en el data set:")
    print(merged_data[duplicates])


# Verificar valores nulos en todas las columnas
null_values = merged_data.isnull().any()
if null_values.any():
    print("Se encontraron valores nulos en el data set:")
    print(merged_data.loc[:, null_values])
else:
    print("No se encontraron valores nulos en el data set.")

# Verificar valores intercambiados entre columnas
column_names = merged_data.columns
for i, col1 in enumerate(column_names[:-1]):
    for col2 in column_names[i+1:]:
        swapped_values = merged_data[(merged_data[col1] == merged_data[col2]) & (merged_data[col1].notnull())]
        if not swapped_values.empty:
            print(f"Se encontraron valores intercambiados entre las columnas '{col1}' y '{col2}':")
            print(swapped_values)


Se encontraron registros duplicados en el data set:
                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    

In [23]:
# Crear una copia del DataFrame original
merged_data_no_duplicates = merged_data.copy()

# Eliminar registros duplicados en el DataFrame original
merged_data.drop_duplicates(inplace=True)

# Crear una copia del DataFrame original sin duplicados
merged_data_no_duplicates = merged_data.drop_duplicates()


## Procedo a crear un df API_data el cual tendra solo los campos que utilizare en la API y asi poder subirlo a github sin problemas

In [24]:
API_data = merged_data_no_duplicates[['id', 'release_date', 'release_year', 'title', 'popularity', 'vote_count', 'vote_average', 'actors', 'director', 'return', 'budget', 'revenue']].copy()


## Corroboramos la estructura de nuestro nuevo data frame 

In [37]:
API_data.head(1)

id release_date release_year      title popularity vote_count  \
0  862   1995-10-30       1995.0  Toy Story  21.946943     5415.0   

  vote_average     actors       director      return      budget      revenue  
0          7.7  Tom Hanks  John Lasseter  12.4518011  30000000.0  373554033.0

In [26]:
API_data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 45369 entries, 0 to 45450
Data columns (total 12 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   id            45369 non-null  object
 1   release_date  45369 non-null  object
 2   release_year  45369 non-null  object
 3   title         45369 non-null  object
 4   popularity    45369 non-null  object
 5   vote_count    45369 non-null  object
 6   vote_average  45369 non-null  object
 7   actors        45369 non-null  object
 8   director      45369 non-null  object
 9   return        45369 non-null  object
 10  budget        45369 non-null  object
 11  revenue       45369 non-null  object
dtypes: object(12)
memory usage: 4.5+ MB


## Corroboramos la consistencia de la data

In [27]:
merged_data_no_duplicates.head(1)

cast  \
0  [{'cast_id': 14, 'character': 'Woody (voice)', 'credit_id': '52fe4284c3a36847f8024f95', 'gender': 2, 'id': 31, 'name': 'Tom Hanks', 'order': 0, 'profile_path': '/pQFoyx7rp09CJTAb932F2g8Nlho.jpg'}, {'cast_id': 15, 'character': 'Buzz Lightyear (voice)', 'credit_id': '52fe4284c3a36847f8024f99', 'gender': 2, 'id': 12898, 'name': 'Tim Allen', 'order': 1, 'profile_path': '/uX2xVf6pMmPepxnvFWyBtjexzgY.jpg'}, {'cast_id': 16, 'character': 'Mr. Potato Head (voice)', 'credit_id': '52fe4284c3a36847f8024f9d', 'gender': 2, 'id': 7167, 'name': 'Don Rickles', 'order': 2, 'profile_path': '/h5BcaDMPRVLHLDzbQavec4xfSdt.jpg'}, {'cast_id': 17, 'character': 'Slinky Dog (voice)', 'credit_id': '52fe4284c3a36847f8024fa1', 'gender': 2, 'id': 12899, 'name': 'Jim Varney', 'order': 3, 'profile_path': '/eIo2jVVXYgjDtaHoF19Ll9vtW7h.jpg'}, {'cast_id': 18, 'character': 'Rex (voice)', 'credit_id': '52fe4284c3a36847f8024fa5', 'gender': 2, 'id': 12900, 'name': 'Wallace Shawn', 'order': 4, 'profile_path': '/oGE6JqPP2xH4tNORKNqxbNPYi7u.jpg'}, {'cast_id': 19, 'character': 'Hamm (voice)', 'credit_id': '52fe4284c3a36847f8024fa9', 'gender': 2, 'id': 7907, 'name': 'John Ratzenberger', 'order': 5, 'profile_path': '/yGechiKWL6TJDfVE2KPSJYqdMsY.jpg'}, {'cast_id': 20, 'character': 'Bo Peep (voice)', 'credit_id': '52fe4284c3a36847f8024fad', 'gender': 1, 'id': 8873, 'name': 'Annie Potts', 'order': 6, 'profile_path': '/eryXT84RL41jHSJcMy4kS3u9y6w.jpg'}, {'cast_id': 26, 'character': 'Andy (voice)', 'credit_id': '52fe4284c3a36847f8024fc1', 'gender': 0, 'id': 1116442, 'name': 'John Morris', 'order': 7, 'profile_path': '/vYGyvK4LzeaUCoNSHtsuqJUY15M.jpg'}, {'cast_id': 22, 'character': 'Sid (voice)', 'credit_id': '52fe4284c3a36847f8024fb1', 'gender': 2, 'id': 12901, 'name': 'Erik von Detten', 'order': 8, 'profile_path': '/twnF1ZaJ1FUNUuo6xLXwcxjayBE.jpg'}, {'cast_id': 23, 'character': 'Mrs. Davis (voice)', 'credit_id': '52fe4284c3a36847f8024fb5', 'gender': 1, 'id': 12133, 'name': 'Laurie Metcalf', 'order': 9, 'profile_path': '/unMMIT60eoBM2sN2nyR7EZ2BvvD.jpg'}, {'cast_id': 24, 'character': 'Sergeant (voice)', 'credit_id': '52fe4284c3a36847f8024fb9', 'gender': 2, 'id': 8655, 'name': 'R. Lee Ermey', 'order': 10, 'profile_path': '/r8GBqFBjypLUP9VVqDqfZ7wYbSs.jpg'}, {'cast_id': 25, 'character': 'Hannah (voice)', 'credit_id': '52fe4284c3a36847f8024fbd', 'gender': 1, 'id': 12903, 'name': 'Sarah Freeman', 'order': 11, 'profile_path': None}, {'cast_id': 27, 'character': 'TV Announcer (voice)', 'credit_id': '52fe4284c3a36847f8024fc5', 'gender': 2, 'id': 37221, 'name': 'Penn Jillette', 'order': 12, 'profile_path': '/zmAaXUdx12NRsssgHbk1T31j2x9.jpg'}]   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        

In [28]:
merged_data_no_duplicates.info()

<class 'pandas.core.frame.DataFrame'>
Index: 45369 entries, 0 to 45450
Data columns (total 24 columns):
 #   Column                 Non-Null Count  Dtype 
---  ------                 --------------  ----- 
 0   cast                   45369 non-null  object
 1   crew                   45369 non-null  object
 2   id                     45369 non-null  object
 3   actors                 45369 non-null  object
 4   director               45369 non-null  object
 5   belongs_to_collection  45369 non-null  object
 6   budget                 45369 non-null  object
 7   genres                 45369 non-null  object
 8   original_language      45369 non-null  object
 9   overview               45369 non-null  object
 10  popularity             45369 non-null  object
 11  production_companies   45369 non-null  object
 12  production_countries   45369 non-null  object
 13  release_date           45369 non-null  object
 14  revenue                45369 non-null  object
 15  runtime                4

## Creo un data frame para mi EDA con las columnas que puedan ser relevantes para mi Analisis exploratorio

In [29]:
columns_to_keep = ['budget', 'genres', 'original_language', 'popularity', 'production_companies',
                   'production_countries', 'release_date', 'revenue', 'runtime', 'spoken_languages',
                   'status', 'title', 'vote_average', 'vote_count', 'release_year', 'return']

EDA_data = merged_data_no_duplicates[columns_to_keep].copy()


In [30]:
EDA_data

budget  \
0      30000000.0   
1      65000000.0   
2             0.0   
3      16000000.0   
4             0.0   
...           ...   
45446         0.0   
45447         0.0   
45448         0.0   
45449         0.0   
45450         0.0   

                                                                                                  genres  \
0       [{'id': 16, 'name': 'Animation'}, {'id': 35, 'name': 'Comedy'}, {'id': 10751, 'name': 'Family'}]   
1      [{'id': 12, 'name': 'Adventure'}, {'id': 14, 'name': 'Fantasy'}, {'id': 10751, 'name': 'Family'}]   
2                                       [{'id': 10749, 'name': 'Romance'}, {'id': 35, 'name': 'Comedy'}]   
3          [{'id': 35, 'name': 'Comedy'}, {'id': 18, 'name': 'Drama'}, {'id': 10749, 'name': 'Romance'}]   
4                                                                         [{'id': 35, 'name': 'Comedy'}]   
...                                                                                                  ...   
45446      [{'id': 18, 'name': 'Drama'}, {'id': 28, 'name': 'Action'}, {'id': 10749, 'name': 'Romance'}]   
45447                                                                      [{'id': 18, 'name': 'Drama'}]   
45448        [{'id': 28, 'name': 'Action'}, {'id': 18, 'name': 'Drama'}, {'id': 53, 'name': 'Thriller'}]   
45449                                                                                                 []   
45450                                                                                                 []   

      original_language popularity  \
0                    en  21.946943   
1                    en  17.015539   
2                    en    11.7129   
3                    en   3.859495   
4                    en   8.387519   
...                 ...        ...   
45446                en   5.683753   
45447                tl   0.178241   
45448                en   0.903007   
45449                en   0.003503   
45450                en   0.163015   

                                                                                                                                                                                                     production_companies  \
0                                                                                                                                                                          [{'name': 'Pixar Animation Studios', 'id': 3}]   
1                                                                                     [{'name': 'TriStar Pictures', 'id': 559}, {'name': 'Teitler Film', 'id': 2550}, {'name': 'Interscope Communications', 'id': 10201}]   
2                                                                                                                                         [{'name': 'Warner Bros.', 'id': 6194}, {'name': 'Lancaster Gate', 'id': 19464}]   
3                                                                                                                                                         [{'name': 'Twentieth Century Fox Film Corporation', 'id': 306}]   
4                                                                                                                            [{'name': 'Sandollar Productions', 'id': 5842}, {'name': 'Touchstone Pictures', 'id': 9195}]   
...                                                                                                                                                                                                                   ...   
45446  [{'name': 'Westdeutscher Rundfunk (WDR)', 'id': 7025}, {'name': 'Working Title Films', 'id': 10163}, {'name': '20th Century Fox Television', 'id': 16323}, {'name': 'CanWest Global Communications', 'id': 38978}]   
45447                                                                                                                                                                              [{'name': 'Sine Olivia', 'id': 19653}]   
45448          

## Expresamos los valores de las columnas correspondientes en miles de millones para poder tener una mejor apreciación de los gráficos 

In [31]:
# Convertir las columnas a tipo numérico
EDA_data['budget (billions)'] = pd.to_numeric(EDA_data['budget'], errors='coerce')
EDA_data['revenue (billions)'] = pd.to_numeric(EDA_data['revenue'], errors='coerce')


# Dividir los valores por mil millones (billones)
EDA_data['budget (billions)'] = EDA_data['budget (billions)'] / 1000000000
EDA_data['revenue (billions)'] = EDA_data['revenue (billions)'] / 1000000000


# Eliminar las columnas originales
EDA_data.drop(['budget', 'revenue'], axis=1, inplace=True)


## VIsualizamos nuestro data frame

In [32]:
EDA_data

genres  \
0       [{'id': 16, 'name': 'Animation'}, {'id': 35, 'name': 'Comedy'}, {'id': 10751, 'name': 'Family'}]   
1      [{'id': 12, 'name': 'Adventure'}, {'id': 14, 'name': 'Fantasy'}, {'id': 10751, 'name': 'Family'}]   
2                                       [{'id': 10749, 'name': 'Romance'}, {'id': 35, 'name': 'Comedy'}]   
3          [{'id': 35, 'name': 'Comedy'}, {'id': 18, 'name': 'Drama'}, {'id': 10749, 'name': 'Romance'}]   
4                                                                         [{'id': 35, 'name': 'Comedy'}]   
...                                                                                                  ...   
45446      [{'id': 18, 'name': 'Drama'}, {'id': 28, 'name': 'Action'}, {'id': 10749, 'name': 'Romance'}]   
45447                                                                      [{'id': 18, 'name': 'Drama'}]   
45448        [{'id': 28, 'name': 'Action'}, {'id': 18, 'name': 'Drama'}, {'id': 53, 'name': 'Thriller'}]   
45449                                                                                                 []   
45450                                                                                                 []   

      original_language popularity  \
0                    en  21.946943   
1                    en  17.015539   
2                    en    11.7129   
3                    en   3.859495   
4                    en   8.387519   
...                 ...        ...   
45446                en   5.683753   
45447                tl   0.178241   
45448                en   0.903007   
45449                en   0.003503   
45450                en   0.163015   

                                                                                                                                                                                                     production_companies  \
0                                                                                                                                                                          [{'name': 'Pixar Animation Studios', 'id': 3}]   
1                                                                                     [{'name': 'TriStar Pictures', 'id': 559}, {'name': 'Teitler Film', 'id': 2550}, {'name': 'Interscope Communications', 'id': 10201}]   
2                                                                                                                                         [{'name': 'Warner Bros.', 'id': 6194}, {'name': 'Lancaster Gate', 'id': 19464}]   
3                                                                                                                                                         [{'name': 'Twentieth Century Fox Film Corporation', 'id': 306}]   
4                                                                                                                            [{'name': 'Sandollar Productions', 'id': 5842}, {'name': 'Touchstone Pictures', 'id': 9195}]   
...                                                                                                                                                                                                                   ...   
45446  [{'name': 'Westdeutscher Rundfunk (WDR)', 'id': 7025}, {'name': 'Working Title Films', 'id': 10163}, {'name': '20th Century Fox Television', 'id': 16323}, {'name': 'CanWest Global Communications', 'id': 38978}]   
45447                                                                                                                                                                              [{'name': 'Sine Olivia', 'id': 19653}]   
45448                                                                                                                                                                   [{'name': 'American World Pictures', 'id': 6165}]   
45449                                                                                                                                 

## Exportamos nuestros data sets con los cambios realizados a un nuevo archivo csv.

In [33]:
merged_data_no_duplicates.to_csv('merged_data.csv', index=False)

In [34]:
API_data.to_csv('api_data.csv', index=False)

In [35]:
EDA_data.to_csv('eda_data.csv', index=False)